In [1]:
# 라이브러리 로드
# requests는 작은 웹브라우저로 웹사이트 내용을 가져온다.
import requests
# BeautifulSoup 을 통해 읽어 온 웹페이지를 파싱한다.
from bs4 import BeautifulSoup as bs
# 크롤링 후 결과를 데이터프레임 형태로 보기 위해 불러온다.
import pandas as pd

from tqdm import trange

In [2]:
# 크롤링 할 사이트
base_url = "https://finance.naver.com/news/news_list.nhn?mode=RANK&page=2"
response = requests.get( base_url )
response

<Response [200]>

In [3]:
soup = bs(response.text, 'html.parser')

content = soup.select("div.hotNewsList")
list_content = str(content).split("\n")

In [33]:
list_result = []

for page in range(10):
    base_url = f"https://finance.naver.com/news/news_list.nhn?mode=RANK&page={page+1}"
    response = requests.get( base_url )
    response
    
    soup = bs(response.text, 'html.parser')

    content = soup.select("div.hotNewsList")
    list_content = str(content).split("\n")
    
    for str_content in list_content:
        if "href" in str_content:
            try:
                head_line = str_content.split('title=')[1]
            except:
                head_line = str_content

            list_result.append(head_line[1:].replace("&quot;","").replace("</a>","").replace("&amp;","&").split('">')[0])
            
list_result = list(set(list_result))

list_result

["65세 이상 인구 8억명 늘어난다…30년간 '데모 테크' 알면 돈 번다 [머니콕]",
 '[마켓인]인천테크노파크, 인천 창업펀드 만든다…운용사 선정 나서',
 "전자상거래 '3강 체제' 재편...공격적 생존경쟁 속도",
 "버진갤럭틱, '우주 관광' 첫 FAA 면허 획득…주가 39% 폭등",
 '[뉴욕증시]예상 부합한 PCE 물가 상승폭…S&P 또 사상 최고',
 '뉴욕증시, 예상 부합한 물가 지표에 상승...S&P500 사상최고',
 '[표]해외 한국 DR 주간등락률',
 '[fn마켓워치]한화솔루션, 타임월드 본점 매각',
 "[종목 현미경]네이버, '인터넷 대장株' 내줬지만…상대적 저평가",
 'LG유플러스, 멤버십 고객에 구독 서비스 확대',
 '테이퍼링·금리인상 예고에도  코스피 사상 첫 3300선 돌파',
 "코스피, 3300시대 '활짝'… 코스닥은 셀트리온 부진에 '미끄럼'",
 '[표]미국 주요기업 주간 등락률',
 '약속지킨 도요타 오너, 자율주행 개발에 사재 500억 출연',
 '[이번주 ETF] 상반기 서학개미가 사랑한 해외 ETF는?',
 '머스크-도시, 다음달 비트코인 논의하기로 합의',
 "[주간사모펀드] 요기요 인수전, 대기업 참여 '미지근'…사모펀드 각축전",
 '[단독]공모가 거품 논란 크래프톤, 청약 내달 21·22일로 연기',
 '해운운임 7주 연속 최고가…수에즈 운하 봉쇄 여파 여전',
 '"SK하이닉스, 실적 개선 본격화...현 시점 주가 빼고 다 좋다"\'>"SK하이닉스, 실적 개선 본격화...현 시점 주가 빼고 다 좋..',
 '[표]해외 한국 DR(6/25).',
 '또 최고치 만든 뉴욕 S&P500 지수...나이키 15% 급등',
 '[속보] 비트코인 8.85% 급락한 3만1718달러에 거래돼',
 '코스피 3300과 2분기 실적시즌 개막',
 '“늙으면 받아주지도 않는다”… 바늘구멍 된 실손보험',
 '늘어나라 고무고무, 그리고 마법의 실(feat. 금호·코오롱)',
 '[주목!e스몰캡]서울옥션, 아시아 미술시장

In [23]:
import pandas as pd
jongmok_list_csv_file = 'jongmok_list.csv'

# 종목 명 딕셔너리 생성
dict_jongmok_nm = {}

# 종목 딕셔너리 생성
def make_jongmok_dict():
    # CSV 데이터 DataFrame으로 추출
    df_jongmok = pd.read_csv(jongmok_list_csv_file, encoding="CP949")
    # DataFrame에서 딕셔너리 생성
    try:
        df_jongmok = df_jongmok[["단축코드", "한글 종목약명"]]
        for index, row in df_jongmok.iterrows():
            dict_jongmok_nm["A" + row["단축코드"]] = row["한글 종목약명"]
    except:
        pass
    
make_jongmok_dict()

dict_jongmok_nm["A000660"]

'SK하이닉스'

In [ ]:
import requests
from bs4 import BeautifulSoup as bs
import pandas as pd

def make_jongmok_dict():
    jongmok_list_csv_file = 'jongmok_list.csv'
    dict_jongmok_nm = {}
    df_jongmok = pd.read_csv(jongmok_list_csv_file, encoding="CP949")
    # DataFrame에서 딕셔너리 생성
    try:
        df_jongmok = df_jongmok[["단축코드", "한글 종목약명"]]
        for index, row in df_jongmok.iterrows():
            dict_jongmok_nm["A" + row["단축코드"]] = row["한글 종목약명"]
    except:
        pass
    
    return dict_jongmok_nm


def remove_char(in_str):
    result_str = in_str.split(">")[2].replace('</span',"").replace(",","")
    
    return result_str


# 최근 10일간의 고가, 저가, 거래량(평균)
def get_prc_vol(cd):
    base_url = f"https://finance.naver.com/item/sise_day.nhn?code={cd}"
    response = requests.get( base_url, headers={"User-agent": "Mozilla/5.0"} )
    soup = bs(response.text, 'html.parser')
    
    gap = 5

    list_end_prc = []
    end_prc_high = 0
    high_prc = 0
    low_prc = 9999999
    vol = 0

    idx = 0
    for href in soup.find("table",{"class":"type2"}).find_all("td"):
        num_val = str(href).replace("\n","")
        if ('<img alt' in num_val or '<td bgcolor' in num_val or '<td colspan="7" height="8"></td>' in num_val): continue
        if '>0</span></td>' in num_val: continue
        if '<td class="num">' not in num_val: continue
        idx += 1
        # 종가
        if idx % gap == 1:
            list_end_prc.append(int(remove_char(num_val)))
            if int(remove_char(num_val)) > end_prc_high:
                end_prc_high = int(remove_char(num_val))
        # 고가
        elif idx % gap == 3:
            try:
                if int(remove_char(num_val)) > high_prc:
                    high_prc = int(remove_char(num_val))
            except:
                high_prc = 0
        # 저가
        elif idx % gap == 4:
            try:
                if int(remove_char(num_val)) < low_prc:
                    low_prc = int(remove_char(num_val))
            except:
                low_prc = 9999999
        # 5의 배수면 거래량
        elif idx % gap == 0:
            try:
                vol += int(remove_char(num_val))
            except:
                vol += 0
#     print(format(high_prc, ","), format(low_prc, ","), format(int(vol / 10), ","))
    inc_cnt = 0
    max_inc_cnt = 0
    for idx in range(9, 1, -1):
        if list_end_prc[idx] > list_end_prc[idx-1]:
            inc_cnt += 1
        else:
            if inc_cnt > max_inc_cnt:
                max_inc_cnt = inc_cnt
            inc_cnt = 0

    max_inc_cnt
    return end_prc_high, high_prc, low_prc, int(vol / 10), max_inc_cnt


list_pos = ["부각","저평가","추천","매력","실적개선","러브콜","수익성개선","수익증대","실적지속","훨훨"]
list_neg = ["그랬을까","고평가","하락","보류","손실증가","부진","미끄럼","저하","우려"]
def get_pos_neg_cnt(row):
    pos_cnt = 0
    neg_cnt = 0
    
    article = row.replace(" ","")
    for pos in list_pos:        
        if pos in article: pos_cnt += 1
    for neg in list_neg:
        if neg in article: neg_cnt += 1
                
    return pos_cnt, neg_cnt


def match_full_name(row, nm):
    row = row.replace('"','').replace(","," ").replace("…"," ").replace("...", " ").replace("·"," ")
    list_row = row.split(" ")
    for val in list_row:
        if nm == val:
            return True
    return False


def get_news():
    list_result = []

    for page in range(10):
        base_url = f"https://finance.naver.com/news/news_list.nhn?mode=RANK&page={page+1}"
        response = requests.get( base_url )
        response

        soup = bs(response.text, 'html.parser')

        content = soup.select("div.hotNewsList")
        list_content = str(content).split("\n")

        for str_content in list_content:
            if "href" in str_content:
                try:
                    head_line = str_content.split('title=')[1]
                except:
                    head_line = str_content

                list_result.append(head_line[1:].replace("&quot;","").replace("</a>","").replace("&amp;","&").split('">')[0])

    list_result = list(set(list_result))
    
    return list_result


list_result = get_news()
dict_jongmok_nm = make_jongmok_dict()
list_whole = []
for cd, nm in dict_jongmok_nm.items():
    for row in list_result:
        print(row)
        list_select = []
        if nm in row:
            if match_full_name(row, nm):
                list_select.append(cd)
                list_select.append(nm)
                list_select.append(row.replace("]","").replace("[",""))
                pos_cnt, neg_cnt = get_pos_neg_cnt(row)
                list_select.append(pos_cnt)
                list_select.append(neg_cnt)
                end_prc_high, high_prc, low_prc, avg_vol, max_inc_cnt = get_prc_vol(cd.replace("A",""))
                list_select.append(end_prc_high)
                list_select.append(max_inc_cnt)
                high_rt = round((high_prc - end_prc_high) / end_prc_high * 100, 2)
                high_rt = 100.00 - high_rt
                list_select.append(high_rt)
                list_select.append(high_prc)
                list_select.append(low_prc)
                gap_75 = int(int((high_prc - low_prc) * 0.85 + low_prc) / 10) * 10
                list_select.append(gap_75)
                list_select.append(avg_vol)
                list_whole.append(list_select)
                
list_cols = ["종목코드", "종목명", "기사", "긍정", "부정", "종가", "종가연속증가", "종가비율", "고가", "저가", "85%", "거래량"]
df_news = pd.DataFrame(list_whole, columns=list_cols)
# df_news = df_news[(df_news.긍정 > df_news.부정) & (df_news.종가 < 100000) & (df_news.거래량 > 100000)]
df_news = df_news.sort_values(by=["종목명"])
# df_news

해운운임 7주 연속 최고가…수에즈 운하 봉쇄 여파 여전
[증시 어디까지 오를까①] 오현석 삼성증권 리서치센터장
[유럽증시] 인플레이션 우려 지속에 혼조
[다음주 증시전망] 3,300 돌파한 코스피, 긴축 불안 떨치며 '서머 랠리' 이어갈까
증권가, 젊은 CEO 효과…'더 편하게, 더 친근하게'
또 최고치 만든 뉴욕 S&P500 지수...나이키 15% 급등
[SK證 주간추천주]수익성 개선 기대…네이버·삼성엔지니어링·피에스케이
하이투자증권, 美주식 수수료 할인·현금 지급 이벤트
중국발 충격 다시 살아나…비트코인 8.5% 급락(상보)
[친절한IB씨] 대우건설 인수전에 깜짝 등판 뒤 사라진 호반···최종 가격 올랐을까
LG유플러스, 멤버십 고객에 구독 서비스 확대
IPO 잰걸음 전자책 플랫폼…'구독의 밀리' vs '웹소설의 리디'
[주목!e해외주식]아마존닷컴, 매력적인 펀더멘털과 업황
머스크-도시, 다음달 비트코인 논의하기로 합의
내일 지자체별 거리두기 단계 발표…당국 "모임 집중 우려"'>내일 지자체별 거리두기 단계 발표…당국 "모임 집중 우려"
[증시 어디까지 오를까③]윤창용 신한금융투자 리서치센터장
전자상거래 '3강 체제' 재편...공격적 생존경쟁 속도
[종목 현미경]네이버, '인터넷 대장株' 내줬지만…상대적 저평가
[표]미국 주요기업 주가(6/25)
[뉴욕마감]S&P 연이틀 사상 최고…일시적 인플레 '방점'
"내가 왜 그랬을까"…카카오 올 98%↑ vs 삼성전자 0.7% 상승'>"내가 왜 그랬을까"…카카오 올 98%↑ vs 삼성전자 0.7%..
뉴욕증시, 물가 지표 안도 속 혼조…S&P 최고치 마감
[주간사모펀드] 요기요 인수전, 대기업 참여 '미지근'…사모펀드 각축전
‘메타버스’가 뭐길래?...은행·증권사, 시장 진출 잇달아
[주목!e스몰캡]서울옥션, 아시아 미술시장의 중심 이동
신문브리핑3 ""노무현 정신을 당 가치로" 친노까지 외연 확장 나선 이준석" 외 주요기사'>신문브리핑3 ""노무현 정신을 당 가치로" 친노까지 외연 확장 ..
尹·李 이어 최재형株까

In [12]:
# 종목의 마감정보 추출
list_jongmok_code = ['005930']
list_cols = ["전일", "고가", "거래량", "시가", "저가", "거래대금"]
list_whole = []
for jongmok_code in list_jongmok_code:
    base_url = "https://finance.naver.com/item/main.nhn?code=" + jongmok_code
    response = requests.get( base_url, headers={"User-agent": "Mozilla/5.0"} )
    soup = bs(response.text, 'html.parser')
    idx = 0
    list_jongmok = []
    for href in soup.find("div",{"class":"rate_info"}).find_all("td"):
        list_href = str(href).split("\n")
        print(list_href)
#         idx += 1
#         key = list_href[1].replace("</span>", "").split(">")[1]
#         val = list_href[3].split("</span>")[0].split(">")[1].replace(",", "")
#         #print(jongmok_code, key, val)
#         list_jongmok.append("20210414")
#         list_jongmok.append(jongmok_code)
#         list_jongmok.append(val)
#         list_whole.append(list_jongmok)
list_whole   

['<td class="first">', '<span class="sptxt sp_txt2">전일</span>', '<em>', '<span class="blind">81,200</span>', '<span class="no8">8</span><span class="no1">1</span><span class="shim">,</span><span class="no2">2</span><span class="no0">0</span><span class="no0">0</span>', '</em>', '</td>']
['<td>', '<span class="sptxt sp_txt4">고가</span>', '<em class="no_up">', '<span class="blind">81,900</span><span class="no8">8</span><span class="no1">1</span><span class="shim">,</span><span class="no9">9</span><span class="no0">0</span><span class="no0">0</span>', '</em>', '<span class="sptxt sp_txt6">(상한가</span>', '<em class="no_cha">', '<span class="blind">105,500</span><span class="no1">1</span><span class="no0">0</span><span class="no5">5</span><span class="shim">,</span><span class="no5">5</span><span class="no0">0</span><span class="no0">0</span>', '</em>', '<span class="sptxt sp_txt8">)</span>', '</td>']
['<td>', '<span class="sptxt sp_txt9">거래량</span>', '<em>', '<span class="blind">12,966,342</

[]

In [90]:
def remove_char(in_str):
    result_str = in_str.split(">")[2].replace('</span',"").replace(",","")
    
    return result_str

base_url = "https://finance.naver.com/item/sise_day.nhn?code=035420"
response = requests.get( base_url, headers={"User-agent": "Mozilla/5.0"} )
soup = bs(response.text, 'html.parser')
# 최근 10일간의 고가, 저가, 거래량(평균)
gap = 5

list_end_prc = []
high_prc = 0
low_prc = 9999999
vol = 0

idx = 0
for href in soup.find("table",{"class":"type2"}).find_all("td"):
    num_val = str(href).replace("\n","")
    if ('<img alt' in num_val or '<td bgcolor' in num_val or '<td colspan="7" height="8"></td>' in num_val): continue
    if '>0</span></td>' in num_val: continue
    if '<td class="num">' not in num_val: continue
    idx += 1
    # 종가
    if idx % gap == 1:
        list_end_prc.append(int(remove_char(num_val)))
    # 고가
    elif idx % gap == 3:
        if int(remove_char(num_val)) > high_prc:
            high_prc = int(remove_char(num_val))
    # 저가
    elif idx % gap == 4:
        if int(remove_char(num_val)) < low_prc:
            low_prc = int(remove_char(num_val))
    # 5의 배수면 거래량
    elif idx % gap == 0:
        vol += int(remove_char(num_val))

print(format(high_prc, ","), format(low_prc, ","), format(int(vol / 10), ","))

inc_cnt = 0
max_inc_cnt = 0
for idx in range(9, 1, -1):
    if list_end_prc[idx] > list_end_prc[idx-1]:
        inc_cnt += 1
    else:
        if inc_cnt > max_inc_cnt:
            max_inc_cnt = inc_cnt
        inc_cnt = 0

print(max_inc_cnt)
print(list_end_prc)

436,000 375,500 1,236,396
2
[410000, 419500, 423500, 391000, 397000, 398000, 389500, 391000, 387000, 387000]
